# Net Liquidity

Net Liquidity is:  

Fed Balance Sheet - Treasury General Account - Reverse Repo = Net Liquidity  

Fed Balance Sheet: https://fred.stlouisfed.org/series/WALCL  
Treasury General Account: https://fred.stlouisfed.org/series/WTREGEN  
Reverse Repo: https://fred.stlouisfed.org/series/WLRRAL

In [1]:
# Inputs
run_min_d = True

In [2]:
import pandas as pd
import yfinance as yf

fed_df = pd.read_csv('./Inputs/FRED_Net_Liquidity/WALCL.csv')
fed_df['DATE'] = pd.to_datetime(fed_df['DATE'])
# display(fed_df.head(2))
tga_df = pd.read_csv('./Inputs/FRED_Net_Liquidity/WTREGEN.csv')
tga_df['DATE'] = pd.to_datetime(tga_df['DATE'])
# display(tga_df.head(2))
rev_df = pd.read_csv('./Inputs/FRED_Net_Liquidity/WLRRAL.csv')
rev_df['DATE'] = pd.to_datetime(rev_df['DATE'])
# display(rev_df.head(2))

data = yf.download(  # or pdr.get_data_yahoo(...
        # tickers list or string as well
        tickers = "BTC-USD SPY",

        # use "period" instead of start/end
        # valid periods: 1d,5d,1mo,3mo,6mo,1y,2y,5y,10y,ytd,max
        # (optional, default is '1mo')
        period = "max",

        # fetch data by interval (including intraday if period < 60 days)
        # valid intervals: 1m,2m,5m,15m,30m,60m,90m,1h,1d,5d,1wk,1mo,3mo
        # (optional, default is '1d')
        interval = "1d",

        # group by ticker (to access via data['SPY'])
        # (optional, default is 'column')
        group_by = 'ticker',

        # adjust all OHLC automatically
        # (optional, default is False)
        auto_adjust = True,

        # download pre/post regular market hours data
        # (optional, default is False)
        prepost = False,

        # use threads for mass downloading? (True/False/Integer)
        # (optional, default is True)
        threads = True,

        # proxy URL scheme use use when downloading?
        # (optional, default is None)
        proxy = None
    )

# display(data.tail(5))

btc_df = data['BTC-USD'][['Close']]
btc_df = btc_df.rename(columns={'Close':'BTC_price'})
# display(btc_df.tail(2))

sp500_df = data['SPY'][['Close']]
sp500_df = sp500_df.rename(columns={'Close':'SP500_price'})
# display(sp500_df.tail(2))

[*********************100%***********************]  2 of 2 completed


#### Functions defined here.

In [3]:
def interpolateData(input_df:pd.Series, ticker_name:str) -> pd.Series:
    
    from collections import defaultdict
    from datetime import datetime, timedelta
    
    col_name = input_df.columns[0]

    input_df = input_df.dropna()
    input_df2 = input_df.reset_index()
    input_array = input_df2.to_numpy()

    # spy_array[0][0] # date
    # spy_array[0][1] # close

    counter = -1

    new_dates_dict = defaultdict(list)
    
#     print(f'len(input_array): {len(input_array)}')

    for x in range(len(input_array)):
        counter += 1
        day_difference = (input_array[x][0] - input_array[x-1][0]).days
#         print(f'x: {x}, day_difference: {day_difference}')

        # Looking for differences in date index that are greater than 1
        if day_difference > 1:
#             print(f"\n{input_array[x][0]}, {counter}, {day_difference}")
            last_non_nan_value = input_array[x][1]
#             print(f"first_non_nan_value: {first_non_nan_value}")
#             print(f"last_non_nan_value: {last_non_nan_value}")

            for y in range(1,day_difference,1):
                calculated_date = input_array[x][0] - timedelta(days=y)
#                 print(f"calculated date: {calculated_date}")
                calculated_price = first_non_nan_value + (last_non_nan_value - first_non_nan_value) * (day_difference - y) / day_difference
#                 print(f"calculated price: {calculated_price}")
                new_dates_dict['date'].append(calculated_date)
                new_dates_dict['price'].append(calculated_price)
                
            # Set the first non nan value equal to the current last non nan value otherwise because the else statement may not get triggered
            first_non_nan_value = last_non_nan_value

        else:
            first_non_nan_value = input_array[x][1]

    try:
        new_dates_df = pd.DataFrame(new_dates_dict)
        new_dates_df = new_dates_df.rename(columns={'date':'Date','price':f'{col_name}'})
        new_dates_df = new_dates_df.set_index('Date')
        complete_df = pd.concat([input_df,new_dates_df])
        complete_df = complete_df.sort_index(axis=0)
#         display(complete_df.tail(30))
        
    except:
        print(f'There are no new added dates for {ticker_name}.')
        complete_df = input_df
    
    return complete_df


# Apply fractional differentiation to BTC and SPY prices
def getWeights_FFD(d,thres):
    w,k=[1.],1
    while True:
        w_=-w[-1] / k*(d-k+1)
        if abs(w_) < thres:break
        w.append(w_);k+=1
    return np.array(w[::-1]).reshape(-1,1)

def fracDiff_FFD(series,d,thres=1e-5):
    # Constant width window (new solution)
#     w,width,df=getWeights_FFD(d,thres),len(w)-1,{}
    w = getWeights_FFD(d,thres)
    width=len(w)-1
    df={}
    for name in series.columns:
        seriesF,df_=series[[name]].fillna(method='ffill').dropna(),pd.Series()
        for iloc1 in range(width,seriesF.shape[0]):
            loc0,loc1=seriesF.index[iloc1-width],seriesF.index[iloc1]
            if not np.isfinite(series.loc[loc1,name]):continue # exclude NAs
            df_[loc1]=np.dot(w.T,seriesF.loc[loc0:loc1])[0,0]
        df[name]=df_.copy(deep=True)
    df=pd.concat(df,axis=1)
    return df


# 5.4 Finding the minimum D value that passes the ADF test
def findMinFFD(df0: pd.Series) -> pd.DataFrame:
    col_name = df0.columns[0]
#     from statsmodels.tsa.stattools import adfuller
#     out=pd.DataFrame(columns=['adfStat','pVal','lags','nObs','95% conf','corr'])
    for e in range(0,105,5):
        d = round(e/100,2)
        print(f'\nd is now: {d}')
        df1=np.log(df0[[col_name]]).resample('1D').last() # downcast to daily obs
#         display(df1)
        df2=fracDiff_FFD(df1,d,thres=.01)
        corr=np.corrcoef(df1.loc[df2.index,col_name],df2[col_name])[0,1]
        print(f'd: {d}, corr: {round(corr,4)}')
        if corr < 0.995:
            d = round(d - 0.05,2)
            break
#         df2=adfuller(df2[col_name],maxlag=1,regression='c',autolag=None)
#         out.loc[d]=list(df2[:4])+[df2[4]['5%']]+[corr] # with critical value
#     out.to_csv('test.csv')
#     plot_df = out[['adfStat','corr']].plot(secondary_y='adfStat')
#     mpl.axhline(out['95% conf'].mean(),linewidth=1,color='r',linestyle='dotted')
#     mpl.savefig('image.png')
    print(f'd min: {d}')
    return d

#### Combine data.

In [4]:
combined_df = pd.merge(fed_df,tga_df,on='DATE',how='left')
combined_df = pd.merge(combined_df,rev_df,on='DATE',how='left')
combined_df = combined_df.rename(columns={'DATE':'Date','WALCL':'FedBalanceSheet','WTREGEN':'TGA','WLRRAL':'RevRepos'})
combined_df['NetLiquidity'] = combined_df['FedBalanceSheet'] - combined_df['TGA'] - combined_df['RevRepos']
combined_df = combined_df.set_index('Date')
combined_df = pd.merge(combined_df,btc_df,left_index=True,right_index=True)
combined_df = pd.merge(combined_df,sp500_df,left_index=True,right_index=True)
combined_df

FedBalanceSheet      TGA  RevRepos  NetLiquidity     BTC_price  \
Date                                                                         
2002-12-18           719542    5.959     21905    697631.041           NaN   
2003-01-08           723762    4.829     18709    705048.171           NaN   
2003-01-15           720074    5.244     17813    702255.756           NaN   
2003-01-22           735953    6.133     18523    717423.867           NaN   
2003-01-29           712809    7.162     18466    694335.838           NaN   
...                     ...      ...       ...           ...           ...   
2022-08-24          8851436  535.267   2494360   6356540.733  21395.019531   
2022-08-31          8826093  612.536   2528284   6297196.464  20049.763672   
2022-09-07          8822401  581.295   2459898   6361921.705  19290.324219   
2022-09-14          8832759  593.808   2526689   6305476.192  20241.089844   
2022-09-21          8816802  692.496   2611368   6204741.504  18547.400391   

            SP500_price  
Date                     
2002-12-18    61.162800  
2003-01-08    62.551662  
2003-01-15    63.242920  
2003-01-22    60.347713  
2003-01-29    59.190987  
...                 ...  
2022-08-24   411.977692  
2022-08-31   393.563293  
2022-09-07   396.152679  
2022-09-14   392.985687  
2022-09-21   377.390015  

[1026 rows x 6 columns]

In [5]:
for col in combined_df.columns:
    combined_df[f'{col}_z'] = (combined_df[f'{col}'] - combined_df[f'{col}'].mean()) / combined_df[f'{col}'].std()

combined_df.tail(5)

FedBalanceSheet      TGA  RevRepos  NetLiquidity     BTC_price  \
Date                                                                         
2022-08-24          8851436  535.267   2494360   6356540.733  21395.019531   
2022-08-31          8826093  612.536   2528284   6297196.464  20049.763672   
2022-09-07          8822401  581.295   2459898   6361921.705  19290.324219   
2022-09-14          8832759  593.808   2526689   6305476.192  20241.089844   
2022-09-21          8816802  692.496   2611368   6204741.504  18547.400391   

            SP500_price  FedBalanceSheet_z     TGA_z  RevRepos_z  \
Date                                                               
2022-08-24   411.977692           2.423785  0.927379    4.791218   
2022-08-31   393.563293           2.412665  1.146148    4.864062   
2022-09-07   396.152679           2.411045  1.057697    4.717218   
2022-09-14   392.985687           2.415590  1.093124    4.860637   
2022-09-21   377.390015           2.408588  1.372535    5.042467   

            NetLiquidity_z  BTC_price_z  SP500_price_z  
Date                                                    
2022-08-24        1.687430     0.527901       2.305239  
2022-08-31        1.657012     0.446247       2.129597  
2022-09-07        1.690188     0.400150       2.154296  
2022-09-14        1.661256     0.457860       2.124088  
2022-09-21        1.609623     0.355057       1.975332

In [6]:
import hvplot.pandas

net_liquidiyt_df = combined_df[['NetLiquidity_z','BTC_price_z','SP500_price_z']]
net_liquidity_plot = net_liquidiyt_df.hvplot.line(title='Net Liquidity v BTC Price v SP500 Price',
                                   grid=True,width=800,height=600)
net_liquidity_plot

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

#### Fractional Differentiation (Weekly)

In [9]:
# interpolated_data = combined_df[['NetLiquidity','BTC_price','SP500_price']]

In [10]:
# # Find the optimum minimum d value
# import numpy as np

# if run_min_d==True:
#     counter = 0
#     min_d_dict = {}

#     for col in interpolated_data.columns:

#         print(f'\nProcessing {col}, {counter+1} of {len(interpolated_data.columns)}...')

#         min_d_dict[col] = findMinFFD(interpolated_data[[col]])

#         counter += 1

#     # print(min_d_dict)

#     from collections import defaultdict

#     min_d_df_convert = defaultdict(list)

#     for k,v in min_d_dict.items():
#         min_d_df_convert['ticker'].append(k)
#         min_d_df_convert['min_d'].append(v)

#     min_d_df = pd.DataFrame(min_d_df_convert)
#     min_d_df.to_csv('./Inputs/min_d_values.csv')

#     print('Completed.')
    
# else:
#     min_d_df = pd.read_csv('./Inputs/min_d_values.csv')
#     min_d_df = min_d_df.drop('Unnamed: 0',axis=1)
# #     display(min_d_df)
    
#     min_d_dict = {}
    
#     for x in range(len(min_d_df)):
#         min_d_dict[min_d_df['ticker'][x]] = min_d_df['min_d'][x]
        
# #     print(min_d_dict)


Processing NetLiquidity, 1 of 3...

d is now: 0.0


C:\Users\srobi\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:78: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.


d: 0.0, corr: 1.0

d is now: 0.05
d: 0.05, corr: 1.0

d is now: 0.1
d: 0.1, corr: 1.0

d is now: 0.15
d: 0.15, corr: 0.9999

d is now: 0.2
d: 0.2, corr: 0.9998

d is now: 0.25
d: 0.25, corr: 0.9996

d is now: 0.3
d: 0.3, corr: 0.9992

d is now: 0.35
d: 0.35, corr: 0.9986

d is now: 0.4
d: 0.4, corr: 0.9979

d is now: 0.45
d: 0.45, corr: 0.9965

d is now: 0.5
d: 0.5, corr: 0.9949
d min: 0.45

Processing BTC_price, 2 of 3...

d is now: 0.0
d: 0.0, corr: 1.0

d is now: 0.05
d: 0.05, corr: 1.0

d is now: 0.1
d: 0.1, corr: 0.9998

d is now: 0.15
d: 0.15, corr: 0.9994

d is now: 0.2
d: 0.2, corr: 0.9987

d is now: 0.25
d: 0.25, corr: 0.9971

d is now: 0.3
d: 0.3, corr: 0.9948
d min: 0.25

Processing SP500_price, 3 of 3...

d is now: 0.0
d: 0.0, corr: 1.0

d is now: 0.05
d: 0.05, corr: 1.0

d is now: 0.1
d: 0.1, corr: 0.9999

d is now: 0.15
d: 0.15, corr: 0.9997

d is now: 0.2
d: 0.2, corr: 0.9994

d is now: 0.25
d: 0.25, corr: 0.9987

d is now: 0.3
d: 0.3, corr: 0.9976

d is now: 0.35
d: 0.3

In [17]:
# # Run the fractional differentiation for the dataframe
# ffd_df = pd.DataFrame()
# counter = 0

# for col in interpolated_data.columns:
    
#     print(f'Processing {col}, {counter+1} of {len(interpolated_data.columns)}...')
    
#     iter_df = fracDiff_FFD(interpolated_data[[col]],min_d_dict[col])
#     display(iter_df)
    
#     if len(ffd_df)==0:
#         ffd_df = iter_df
#     else:
#         ffd_df = pd.concat([ffd_df,iter_df],axis=1)
        
#     counter += 1

# # btc_ffd = fracDiff_FFD(btc_series,0.35)
# # spy_ffd = fracDiff_FFD(spy_series,0.35)

# # combined_df = pd.merge(btc_ffd,spy_ffd,left_index=True,right_index=True,how='outer')
# # combined_df = pd.merge(combined_df,int_rate_data,left_index=True,right_index=True,how='outer')

Processing NetLiquidity, 1 of 3...


C:\Users\srobi\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:78: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.


Empty DataFrame
Columns: [NetLiquidity]
Index: []

Processing BTC_price, 2 of 3...


C:\Users\srobi\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:78: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.


Empty DataFrame
Columns: [BTC_price]
Index: []

Processing SP500_price, 3 of 3...


C:\Users\srobi\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:78: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.


Empty DataFrame
Columns: [SP500_price]
Index: []

In [12]:
# # Obtain z_scores for all columns
# z_score_col_list = []
# counter = 0

# for col in ffd_df.columns:
#     print(f'Processing {col}, {counter+1} of {len(ffd_df.columns)}...')
#     new_col_name = f'{col}_z'
#     z_score_col_list.append(new_col_name)
#     ffd_df[new_col_name] = (ffd_df[col] - ffd_df[col].mean()) / ffd_df[col].std()
#     counter += 1

# ffd_z_df = ffd_df[z_score_col_list]

Processing SP500_price, 1 of 1...


In [13]:
# import hvplot.pandas

# market_overview_plot = ffd_z_df.hvplot.line(title='Market Overview',
#                                    grid=True,width=800,height=600)

# print('Below chart data is based on fractionally differentiated price series data and then transformed to Z-scores for comparison purposes.')

# market_overview_plot

Below chart data is based on fractionally differentiated price series data and then transformed to Z-scores for comparison purposes.


:Curve   [index]   (SP500_price_z)

#### Fractional Differentiation (Daily)

This section joins the dataframes using 'outer' instead of 'inner' join to include the daily timeframe data.

In [12]:
combined_df = pd.merge(fed_df,tga_df,on='DATE',how='left')
combined_df = pd.merge(combined_df,rev_df,on='DATE',how='left')
combined_df = combined_df.rename(columns={'DATE':'Date','WALCL':'FedBalanceSheet','WTREGEN':'TGA','WLRRAL':'RevRepos'})
combined_df['NetLiquidity'] = combined_df['FedBalanceSheet'] - combined_df['TGA'] - combined_df['RevRepos']
combined_df = combined_df.set_index('Date')
combined_df = pd.merge(combined_df,btc_df,left_index=True,right_index=True,how='outer')
combined_df = pd.merge(combined_df,sp500_df,left_index=True,right_index=True,how='outer')
combined_df

FedBalanceSheet      TGA   RevRepos  NetLiquidity     BTC_price  \
Date                                                                          
1993-01-29              NaN      NaN        NaN           NaN           NaN   
1993-02-01              NaN      NaN        NaN           NaN           NaN   
1993-02-02              NaN      NaN        NaN           NaN           NaN   
1993-02-03              NaN      NaN        NaN           NaN           NaN   
1993-02-04              NaN      NaN        NaN           NaN           NaN   
...                     ...      ...        ...           ...           ...   
2022-09-20              NaN      NaN        NaN           NaN  18890.789062   
2022-09-21        8816802.0  692.496  2611368.0   6204741.504  18547.400391   
2022-09-22              NaN      NaN        NaN           NaN  19413.550781   
2022-09-23              NaN      NaN        NaN           NaN  19297.638672   
2022-09-24              NaN      NaN        NaN           NaN  19086.896484   

            SP500_price  
Date                     
1993-01-29    25.334038  
1993-02-01    25.514206  
1993-02-02    25.568270  
1993-02-03    25.838552  
1993-02-04    25.946657  
...                 ...  
2022-09-20   384.089996  
2022-09-21   377.390015  
2022-09-22   374.220001  
2022-09-23   367.950012  
2022-09-24          NaN  

[8384 rows x 6 columns]

In [13]:
# Interpolate the dataframe to fill in missing data points
interpolated_data = pd.DataFrame()
counter = 0

combined_df = combined_df[['NetLiquidity','BTC_price','SP500_price']]

for col in combined_df.columns:
    
    print(f'Processing {col}, {counter+1} of {len(combined_df.columns)}...')
#     col_name = ism_data.columns[counter]
    iter_df = interpolateData(combined_df[[col]],col)
    
    if len(interpolated_data)==0:
        interpolated_data = iter_df
    else:
        interpolated_data = pd.concat([interpolated_data,iter_df],axis=1)
        
    counter += 1

Processing NetLiquidity, 1 of 3...
Processing BTC_price, 2 of 3...
There are no new added dates for BTC_price.
Processing SP500_price, 3 of 3...


In [14]:
# Find the optimum minimum d value
import numpy as np

if run_min_d==True:
    counter = 0
    min_d_dict = {}

    for col in interpolated_data.columns:

        print(f'\nProcessing {col}, {counter+1} of {len(interpolated_data.columns)}...')

        min_d_dict[col] = findMinFFD(interpolated_data[[col]])

        counter += 1

    # print(min_d_dict)

    from collections import defaultdict

    min_d_df_convert = defaultdict(list)

    for k,v in min_d_dict.items():
        min_d_df_convert['ticker'].append(k)
        min_d_df_convert['min_d'].append(v)

    min_d_df = pd.DataFrame(min_d_df_convert)
    min_d_df.to_csv('./Inputs/min_d_values.csv')

    print('Completed.')
    
else:
    min_d_df = pd.read_csv('./Inputs/min_d_values.csv')
    min_d_df = min_d_df.drop('Unnamed: 0',axis=1)
#     display(min_d_df)
    
    min_d_dict = {}
    
    for x in range(len(min_d_df)):
        min_d_dict[min_d_df['ticker'][x]] = min_d_df['min_d'][x]
        
#     print(min_d_dict)


Processing NetLiquidity, 1 of 3...

d is now: 0.0


C:\Users\srobi\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:78: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.


d: 0.0, corr: 1.0

d is now: 0.05
d: 0.05, corr: 1.0

d is now: 0.1
d: 0.1, corr: 1.0

d is now: 0.15
d: 0.15, corr: 1.0

d is now: 0.2
d: 0.2, corr: 1.0

d is now: 0.25
d: 0.25, corr: 0.9999

d is now: 0.3
d: 0.3, corr: 0.9999

d is now: 0.35
d: 0.35, corr: 0.9999

d is now: 0.4
d: 0.4, corr: 0.9998

d is now: 0.45
d: 0.45, corr: 0.9997

d is now: 0.5
d: 0.5, corr: 0.9996

d is now: 0.55
d: 0.55, corr: 0.9996

d is now: 0.6
d: 0.6, corr: 0.9993

d is now: 0.65
d: 0.65, corr: 0.9992

d is now: 0.7
d: 0.7, corr: 0.999

d is now: 0.75
d: 0.75, corr: 0.9984

d is now: 0.8
d: 0.8, corr: 0.998

d is now: 0.85
d: 0.85, corr: 0.9974

d is now: 0.9
d: 0.9, corr: 0.9962

d is now: 0.95
d: 0.95, corr: 0.9923
d min: 0.9

Processing BTC_price, 2 of 3...

d is now: 0.0
d: 0.0, corr: 1.0

d is now: 0.05
d: 0.05, corr: 1.0

d is now: 0.1
d: 0.1, corr: 1.0

d is now: 0.15
d: 0.15, corr: 0.9999

d is now: 0.2
d: 0.2, corr: 0.9997

d is now: 0.25
d: 0.25, corr: 0.9994

d is now: 0.3
d: 0.3, corr: 0.9989

In [15]:
# Run the fractional differentiation for the dataframe
ffd_df = pd.DataFrame()
counter = 0

for col in interpolated_data.columns:
    
    print(f'Processing {col}, {counter+1} of {len(interpolated_data.columns)}...')
    
    iter_df = fracDiff_FFD(interpolated_data[[col]],min_d_dict[col])
    
    if len(ffd_df)==0:
        ffd_df = iter_df
    else:
        ffd_df = pd.concat([ffd_df,iter_df],axis=1)
        
    counter += 1

# btc_ffd = fracDiff_FFD(btc_series,0.35)
# spy_ffd = fracDiff_FFD(spy_series,0.35)

# combined_df = pd.merge(btc_ffd,spy_ffd,left_index=True,right_index=True,how='outer')
# combined_df = pd.merge(combined_df,int_rate_data,left_index=True,right_index=True,how='outer')

Processing NetLiquidity, 1 of 3...


C:\Users\srobi\anaconda3\envs\pyvizenv\lib\site-packages\ipykernel_launcher.py:78: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.


Processing BTC_price, 2 of 3...
Processing SP500_price, 3 of 3...


In [16]:
# Obtain z_scores for all columns
z_score_col_list = []
counter = 0

for col in ffd_df.columns:
    print(f'Processing {col}, {counter+1} of {len(ffd_df.columns)}...')
    new_col_name = f'{col}_z'
    z_score_col_list.append(new_col_name)
    ffd_df[new_col_name] = (ffd_df[col] - ffd_df[col].mean()) / ffd_df[col].std()
    counter += 1

ffd_z_df = ffd_df[z_score_col_list]

Processing NetLiquidity, 1 of 3...
Processing BTC_price, 2 of 4...
Processing SP500_price, 3 of 5...


In [17]:
import hvplot.pandas

market_overview_plot = ffd_z_df.hvplot.line(title='Market Overview',
                                   grid=True,width=800,height=600)

print('Below chart data is based on fractionally differentiated price series data and then transformed to Z-scores for comparison purposes.')

market_overview_plot

Below chart data is based on fractionally differentiated price series data and then transformed to Z-scores for comparison purposes.


:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [18]:
import datetime

print(f'Completed on {datetime.datetime.now()}.')

Completed on 2022-09-24 13:10:00.357478.
